In [0]:
sc

SparkContext 

 Spark UI 

 
 Version 
 v3.3.2 
 Master 
 local[8] 
 AppName 
 Databricks Shell

In [0]:
from pyspark.sql import SparkSession

spark = SparkSession.builder \
        .appName('BronzeLayer') \
        .getOrCreate()

In [0]:
spark

SparkSession - hive 
 
 
 SparkContext 

 Spark UI 

 
 Version 
 v3.3.2 
 Master 
 local[8] 
 AppName 
 Databricks Shell

In [0]:
pip install azure-storage-file-datalake

Python interpreter will be restarted.
  Attempting uninstall: typing-extensions
    Found existing installation: typing-extensions 4.1.1
    Not uninstalling typing-extensions at /databricks/python3/lib/python3.9/site-packages, outside environment /local_disk0/.ephemeral_nfs/envs/pythonEnv-038fbab6-6856-4397-a5b8-4da1660ee204
    Can't uninstall 'typing-extensions'. No files were found to uninstall.
Python interpreter will be restarted.


In [0]:
import json
from azure.storage.filedatalake import DataLakeServiceClient, FileSystemClient, DataLakeFileClient
 
CONNECTION_STRING = "DefaultEndpointsProtocol=https;AccountName=swiggycasestudysa;AccountKey=I1jjhNZYL2dShfUqgqYawj7U53guZLOyG1SbQ407oMflGToAzGXJ3ubw2Qi0oyBanQiidJQciAIS+AStDdpJrQ==;EndpointSuffix=core.windows.net"
ACCOUNT_KEY = "I1jjhNZYL2dShfUqgqYawj7U53guZLOyG1SbQ407oMflGToAzGXJ3ubw2Qi0oyBanQiidJQciAIS+AStDdpJrQ=="
ACCOUNT_NAME = "swiggycasestudysa"
 
# Initialize DataLakeServiceClient for Azure Data Lake Storage Gen2
data_lake_service_client = DataLakeServiceClient.from_connection_string(CONNECTION_STRING)
 
# Name of the filesystem (similar to container) where files are stored
file_system_name = "data"
 
 
def download_and_parse_json(file_system_name, file_path):
    file_client = data_lake_service_client.get_file_system_client(file_system_name).get_file_client(file_path)
    try:
        # Download the JSON data as bytes
        file_data = file_client.download_file().readall()
       
        # Decode the bytes to a string and load it as JSON
        json_data = json.loads(file_data.decode('utf-8'))
       
        print("JSON data successfully retrieved and parsed")
        return json_data
    except Exception as e:
        print(f"Failed to download and parse JSON: {e}")
        return None
 
if __name__ == "__main__":
 
    data = download_and_parse_json("data", "swiggy.json")
    if data:
        print("fetch completed")
   
 

JSON data successfully retrieved and parsed
fetch completed


In [0]:
records_restaurant = []
records_menu = []
 
# Loop through the top-level cities
for city_name, city_data in data.items():
    # If the city has sub-areas (nested cities), loop through them
    if isinstance(city_data, dict) and 'restaurants' in city_data:
        # No sub-area: directly process the city
        full_city_name = city_name
       
        # Loop through restaurants in the city
        for restaurant_id, restaurant_data in city_data.get('restaurants', {}).items():
            records_restaurant.append({
                'restaurant_id': restaurant_id,
                'name': restaurant_data.get('name'),
                'city': full_city_name,
                'rating': restaurant_data.get('rating'),
                'rating_count': restaurant_data.get('rating_count'),
                'cost': restaurant_data.get('cost'),
                'cuisine': restaurant_data.get('cuisine'),
                'lic_no': restaurant_data.get('lic_no'),
                'link': restaurant_data.get('link'),
                'address': restaurant_data.get('address'),
            })
 
            # Loop through menu categories for the current restaurant
            for category, items in restaurant_data.get('menu', {}).items():
                # Loop through items in each category
                for item_name, item_data in items.items():
                    records_menu.append({
                        'restaurant_id': restaurant_id,
                        'category': category,
                        'item_name': item_name,
                        'price': item_data.get('price'),
                        'veg_or_non_veg': item_data.get('veg_or_non_veg')
                    })
   
    # If the city has sub-areas (nested cities), process each sub-area
    elif isinstance(city_data, dict):
        for sub_area_name, sub_area_data in city_data.items():
            full_city_name = f"{sub_area_name}, {city_name}"
 
            # Loop through restaurants in the sub-area
            for restaurant_id, restaurant_data in sub_area_data.get('restaurants', {}).items():
                records_restaurant.append({
                    'restaurant_id': restaurant_id,
                    'name': restaurant_data.get('name'),
                    'city': full_city_name,
                    'rating': restaurant_data.get('rating'),
                    'rating_count': restaurant_data.get('rating_count'),
                    'cost': restaurant_data.get('cost'),
                    'cuisine': restaurant_data.get('cuisine'),
                    'lic_no': restaurant_data.get('lic_no'),
                    'link': restaurant_data.get('link'),
                    'address': restaurant_data.get('address'),
                })
 
                # Loop through menu categories for the current restaurant
                for category, items in restaurant_data.get('menu', {}).items():
                    # Loop through items in each category
                    for item_name, item_data in items.items():
                        records_menu.append({
                            'restaurant_id': restaurant_id,
                            'category': category,
                            'item_name': item_name,
                            'price': item_data.get('price'),
                            'veg_or_non_veg': item_data.get('veg_or_non_veg'),
                        })
 
# Convert to Spark DataFrames
restaurant_df = spark.createDataFrame(records_restaurant)
menu_df = spark.createDataFrame(records_menu)
 


In [0]:
restaurant_df.show()

+--------------------+------+-----+--------------------+--------------+--------------------+--------------------+------+---------------+-------------+
|             address|  city| cost|             cuisine|        lic_no|                link|                name|rating|   rating_count|restaurant_id|
+--------------------+------+-----+--------------------+--------------+--------------------+--------------------+------+---------------+-------------+
|AB FOODS POINT, N...|Abohar|₹ 200|    Beverages,Pizzas|22122652000138|https://www.swigg...|      AB FOODS POINT|    --|Too Few Ratings|       567335|
|Janta Sweet House...|Abohar|₹ 200|       Sweets,Bakery|12117201000112|https://www.swigg...|   Janta Sweet House|   4.4|    50+ ratings|       531342|
|theka coffee desi...|Abohar|₹ 100|           Beverages|22121652000190|https://www.swigg...|   theka coffee desi|   3.8|   100+ ratings|       158203|
|Singh Hut, CIRCUL...|Abohar|₹ 250|    Fast Food,Indian|22119652000167|https://www.swigg...|  

In [0]:
menu_df.show()

+-----------------+--------------------+-----+-------------+--------------+
|         category|           item_name|price|restaurant_id|veg_or_non_veg|
+-----------------+--------------------+-----+-------------+--------------+
|           Burger|   Aloo Tikki Burger|   40|       567335|           Veg|
|           Burger|   Veg Creamy Burger|   50|       567335|           Veg|
|           Burger| Cheese Burst Burger|   65|       567335|           Veg|
|           Burger|Paneer Creamy Burger|   80|       567335|           Veg|
|           Burger|      Maxican Burger|   80|       567335|           Veg|
|           Burger|  Bbq Chicken Burger|  105|       567335|       Non-veg|
|           Burger|Peri Peri Chicken...|  105|       567335|       Non-veg|
|   Pasta Must Try|         White Sauce|  100|       567335|           Veg|
|   Pasta Must Try|           Red Sauce|  100|       567335|           Veg|
|   Pasta Must Try|          Pink Sauce|  125|       567335|           Veg|
|   Pasta Mu

In [0]:
restaurant_df.printSchema()

root
 |-- address: string (nullable = true)
 |-- city: string (nullable = true)
 |-- cost: string (nullable = true)
 |-- cuisine: string (nullable = true)
 |-- lic_no: string (nullable = true)
 |-- link: string (nullable = true)
 |-- name: string (nullable = true)
 |-- rating: string (nullable = true)
 |-- rating_count: string (nullable = true)
 |-- restaurant_id: string (nullable = true)



In [0]:
menu_df.printSchema()

root
 |-- category: string (nullable = true)
 |-- item_name: string (nullable = true)
 |-- price: string (nullable = true)
 |-- restaurant_id: string (nullable = true)
 |-- veg_or_non_veg: string (nullable = true)



In [0]:
restaurant_df.count()

Out[7]: 181404

In [0]:
menu_df.count()

Out[8]: 13379782

# 1. Data Cleaning: Nulls and Duplicates

Clean restaurant_df

In [0]:
from pyspark.sql.functions import col

duplicates = restaurant_df.groupBy("Restaurant_ID").count().filter(col("count") > 1).count()
duplicates

Out[9]: 19530

In [0]:
restaurant_df.filter(col('Restaurant_ID')=='494244').show()

+--------------------+--------------------+-----+----------------+--------------+--------------------+------------+------+---------------+-------------+
|             address|                city| cost|         cuisine|        lic_no|                link|        name|rating|   rating_count|restaurant_id|
+--------------------+--------------------+-----+----------------+--------------+--------------------+------------+------+---------------+-------------+
|Big Sandwich, SHO...|Vastrapur, Ahmedabad|₹ 200|Snacks,Beverages|20722038000617|https://www.swigg...|Big Sandwich|    --|Too Few Ratings|       494244|
|                null|     link, Ahmedabad| null|            null|          null|big-sandwich-vast...|Big Sandwich|    --|           null|       494244|
+--------------------+--------------------+-----+----------------+--------------+--------------------+------------+------+---------------+-------------+



In [0]:
from pyspark.sql.functions import * 

restaurant_df.groupBy("City").agg(count("City").alias("City_count")).count()

Out[11]: 865

In [0]:
# Drop duplicates
restaurant_df_dropped = restaurant_df.dropDuplicates(["Restaurant_ID"])

In [0]:
restaurant_df_dropped.count()

Out[13]: 160621

In [0]:
from pyspark.sql.functions import col, sum


null_count_df = restaurant_df_dropped.select([sum(col(c).isNull().cast("int")).alias(c) for c in restaurant_df_dropped.columns])


null_count_df.show()

+-------+----+-----+-------+------+----+----+------+------------+-------------+
|address|city| cost|cuisine|lic_no|link|name|rating|rating_count|restaurant_id|
+-------+----+-----+-------+------+----+----+------+------------+-------------+
|  12031|   0|12031|  12031| 12031|   0|   0|     0|       12031|            0|
+-------+----+-----+-------+------+----+----+------+------------+-------------+



In [0]:
restaurant_df_dropped2 = restaurant_df_dropped.dropna()

In [0]:
restaurant_df_dropped2.count()

Out[16]: 148590

In [0]:
from pyspark.sql.functions import col, sum


null_count_df = restaurant_df_dropped2.select([sum(col(c).isNull().cast("int")).alias(c) for c in restaurant_df_dropped2.columns])


null_count_df.show()

+-------+----+----+-------+------+----+----+------+------------+-------------+
|address|city|cost|cuisine|lic_no|link|name|rating|rating_count|restaurant_id|
+-------+----+----+-------+------+----+----+------+------------+-------------+
|      0|   0|   0|      0|     0|   0|   0|     0|           0|            0|
+-------+----+----+-------+------+----+----+------+------------+-------------+



Clean menu_df

In [0]:
from pyspark.sql.functions import col, sum


null_count_df_menu = menu_df.select([sum(col(c).isNull().cast("int")).alias(c) for c in menu_df.columns])


null_count_df_menu.show()

+--------+---------+-----+-------------+--------------+
|category|item_name|price|restaurant_id|veg_or_non_veg|
+--------+---------+-----+-------------+--------------+
|       0|        0|    0|            0|             0|
+--------+---------+-----+-------------+--------------+



In [0]:
duplicates_menu_df = menu_df.groupBy("restaurant_id","category","item_name").count().filter(col("count") > 1)
duplicates_menu_df.count()

Out[19]: 559515

In [0]:
# Drop duplicates
menu_df_dropped = menu_df.dropDuplicates(["restaurant_id","item_name","category"])


In [0]:
menu_df_dropped.count()

Out[21]: 12750923

In [0]:
restaurant_df_dropped2.count()

Out[22]: 148590

In [0]:
restaurant_df_dropped2.show()

+--------------------+--------------------+------+--------------------+--------------+--------------------+--------------------+------+---------------+-------------+
|             address|                city|  cost|             cuisine|        lic_no|                link|                name|rating|   rating_count|restaurant_id|
+--------------------+--------------------+------+--------------------+--------------+--------------------+--------------------+------+---------------+-------------+
|Coffee Culture, 3...|Vastrapur, Ahmedabad| ₹ 350|       Pizzas,Pastas|10721026000846|https://www.swigg...|      Coffee Culture|   4.6|    20+ ratings|       100010|
|Tamanna Executive...|     Hinjewadi, Pune| ₹ 500|North Indian,Chinese|11518036001587|https://www.swigg...|   Tamanna Executive|   4.2|   100+ ratings|        10010|
|Snack Shack Sandw...| Shivaji Nagar, Pune| ₹ 150|              Indian|21519157000001|https://www.swigg...|Snack Shack Sandwich|    --|Too Few Ratings|       100213|
|Cha

In [0]:
menu_df_dropped.show()

+--------------------+--------------------+-----+-------------+--------------+
|            category|           item_name|price|restaurant_id|veg_or_non_veg|
+--------------------+--------------------+-----+-------------+--------------+
|         Recommended|     Arrabiata Pasta|  325|       100010|           Veg|
|               Pizza| Cheese Garlic Bread|  150|       100010|           Veg|
|             Burgers|Crispy Paneer Burger|  275|       100010|           Veg|
|         Recommended| Grilled Veggie Wich|  195|       100010|           Veg|
|         Cold Coffee|Iced Cappuccino C...|  200|       100010|           Veg|
|         Cold Coffee|Koffee Kulture Co...|  175|       100010|           Veg|
|               Mains|Manchurian Gravy ...|  275|       100010|           Veg|
|         Recommended|        Mexican Rice|  295|       100010|           Veg|
|         Recommended|  Nutella Cappuccino|  275|       100010|           Veg|
|Sinful Chocolate ...|   Oreo Cookie Shake|  300|   

# 2. Schema Consistency and Data Type Standardization

In [0]:
from pyspark.sql.functions import col, sum

null_count_df = restaurant_df_dropped2.select([sum(col(c).isNull().cast("int")).alias(c) for c in restaurant_df_dropped2.columns])
null_count_df.show()

+-------+----+----+-------+------+----+----+------+------------+-------------+
|address|city|cost|cuisine|lic_no|link|name|rating|rating_count|restaurant_id|
+-------+----+----+-------+------+----+----+------+------------+-------------+
|      0|   0|   0|      0|     0|   0|   0|     0|           0|            0|
+-------+----+----+-------+------+----+----+------+------------+-------------+



In [0]:
restaurant_df_dropped2.filter(col("name") == "NA").show(truncate=False)


+-------+------------------------------+----+-------+------+---------------------------------------------------------------------------------------------------------+----+------+------------+-------------+
|address|city                          |cost|cuisine|lic_no|link                                                                                                     |name|rating|rating_count|restaurant_id|
+-------+------------------------------+----+-------+------+---------------------------------------------------------------------------------------------------------+----+------+------------+-------------+
|NA     |George Town, Chennai          |NA  |NA     |NA    |https://www.swiggy.com/restaurants/meet-my-bread-portuguese-church-street-george-town-chennai-140189     |NA  |NA    |NA          |140189       |
|NA     |Rohini, Delhi                 |NA  |NA     |NA    |https://www.swiggy.com/restaurants/chef-brothers-shawarma-roll-community-center-sec-9-rohini-delhi-167737|NA  |NA   

In [0]:
restaurant_df_dropped2 = restaurant_df_dropped2.filter(col("name") != "NA")

In [0]:
restaurant_df_dropped2.show()

+--------------------+--------------------+------+--------------------+--------------+--------------------+--------------------+------+---------------+-------------+
|             address|                city|  cost|             cuisine|        lic_no|                link|                name|rating|   rating_count|restaurant_id|
+--------------------+--------------------+------+--------------------+--------------+--------------------+--------------------+------+---------------+-------------+
|Coffee Culture, 3...|Vastrapur, Ahmedabad| ₹ 350|       Pizzas,Pastas|10721026000846|https://www.swigg...|      Coffee Culture|   4.6|    20+ ratings|       100010|
|Tamanna Executive...|     Hinjewadi, Pune| ₹ 500|North Indian,Chinese|11518036001587|https://www.swigg...|   Tamanna Executive|   4.2|   100+ ratings|        10010|
|Snack Shack Sandw...| Shivaji Nagar, Pune| ₹ 150|              Indian|21519157000001|https://www.swigg...|Snack Shack Sandwich|    --|Too Few Ratings|       100213|
|Cha

In [0]:
restaurant_df_dropped2.select(col("rating_count")).distinct().display()

rating_count 20+ ratings 100+ ratings 10K+ ratings 5K+ ratings 1K+ ratings 500+ ratings Too Few Ratings 50+ ratings

In [0]:

from pyspark.sql.functions import col, regexp_extract, when, lit, split, lower, current_timestamp,trim



# # Replace invalid or non-numeric 'Cost' values (e.g., "NA", "") with 0
# restaurant_df_new = restaurant_df_dropped2.withColumn(
#     "Cost",
#     when(
#         (trim(col("Cost")).isNotNull()) & 
#         (trim(col("Cost")) != "") & 
#         (~col("Cost").isin("NA", "N/A", "na", "null")) & 
#         (regexp_extract(col("Cost"), r'(\d+)', 1) != ""),
#         regexp_extract(col("Cost"), r'(\d+)', 1).cast("int")
#     ).otherwise(0)
# )

# Convert 'Cost' to numeric in restaurant_df
restaurant_df_new = restaurant_df_dropped2.withColumn("cost", 
    when(col("cost").isNotNull(), regexp_extract("cost", r'(\d+)', 1).cast("int")).otherwise(None))

# Convert 'Rating' to float, replace '--' with 0
restaurant_df_new = restaurant_df_new.withColumn("rating",
    when(col("rating") == "--", None).otherwise(col("rating").cast("float")))

# restaurant_df_new = restaurant_df_new.withColumn(
#     "Rating_Count",
#     when(
#         (trim(col("Rating_Count")).isNull()) | 
#         (trim(col("Rating_Count")) == "") | 
#         (col("Rating_Count").isin("NA", "N/A", "--", "null", "na", "Null", "NULL")) |
#         (regexp_extract(col("Rating_Count"), r'(\d+)', 0) == ""),
#         0
#     ).otherwise(
#         regexp_extract(col("Rating_Count"), r'(\d+)', 0).cast("int")
#     )
# )

# Convert 'rating_count' to numeric, handling 'K' suffix (e.g., 1K -> 1000, 5K -> 5000)
restaurant_df_new = restaurant_df_new.withColumn(
    "rating_count",
    when(
        regexp_extract("rating_count", r'(\d+)K', 1) != "",  # Check for 'K' suffixed ratings
        (regexp_extract("rating_count", r'(\d+)K', 1).cast("int") * 1000)  # Multiply by 1000
    ).when(
        regexp_extract("rating_count", r'(\d+)', 1) != "",  # For regular numeric values without 'K'
        regexp_extract("rating_count", r'(\d+)', 1).cast("int")  # Cast directly to int
    ).otherwise(None)  # For cases like 'Too Few Ratings', set to None
)



# Convert 'Price' to numeric in menu_df
menu_df_new = menu_df_dropped.withColumn("price", col("price").cast("float"))

# Standardize 'Veg_or_Non_Veg' to lowercase
menu_df_new = menu_df_new.withColumn("veg_or_non_veg", lower(col("veg_or_non_veg")))

# Display the schema
restaurant_df_new.printSchema()
menu_df_new.printSchema()

root
 |-- address: string (nullable = true)
 |-- city: string (nullable = true)
 |-- cost: integer (nullable = true)
 |-- cuisine: string (nullable = true)
 |-- lic_no: string (nullable = true)
 |-- link: string (nullable = true)
 |-- name: string (nullable = true)
 |-- rating: float (nullable = true)
 |-- rating_count: integer (nullable = true)
 |-- restaurant_id: string (nullable = true)

root
 |-- category: string (nullable = true)
 |-- item_name: string (nullable = true)
 |-- price: float (nullable = true)
 |-- restaurant_id: string (nullable = true)
 |-- veg_or_non_veg: string (nullable = true)



In [0]:
restaurant_df_new.select(col("rating_count")).distinct().display()

rating_count null 5000 20 500 10000 100 1000 50

In [0]:
# Drop the 'City_Link' column
restaurant_df_new = restaurant_df_new.drop("link")

# Verify the result
restaurant_df_new.printSchema()
restaurant_df_new.show(truncate=False)


root
 |-- address: string (nullable = true)
 |-- city: string (nullable = true)
 |-- cost: integer (nullable = true)
 |-- cuisine: string (nullable = true)
 |-- lic_no: string (nullable = true)
 |-- name: string (nullable = true)
 |-- rating: float (nullable = true)
 |-- rating_count: integer (nullable = true)
 |-- restaurant_id: string (nullable = true)

+-----------------------------------------------------------------------------------------------------------------------------------+------------------------------------+----+----------------------+--------------+-----------------------+------+------------+-------------+
|address                                                                                                                            |city                                |cost|cuisine               |lic_no        |name                   |rating|rating_count|restaurant_id|
+-------------------------------------------------------------------------------------------------

In [0]:
from pyspark.sql.functions import col, sum

null_count_df = restaurant_df_new.select([sum(col(c).isNull().cast("int")).alias(c) for c in restaurant_df_new.columns])
null_count_df.show()

+-------+----+----+-------+------+----+------+------------+-------------+
|address|city|cost|cuisine|lic_no|name|rating|rating_count|restaurant_id|
+-------+----+----+-------+------+----+------+------------+-------------+
|      0|   0|  45|      0|     0|   0| 87118|       87118|            0|
+-------+----+----+-------+------+----+------+------------+-------------+



In [0]:
from pyspark.sql.functions import col, avg, when

# Step 1: Calculate average cost per city
avg_cost_by_city = restaurant_df_new.groupBy("city").agg(avg("cost").alias("avg_cost"))

# Step 2: Join the original DataFrame with the average cost DataFrame
restaurant_df_with_avg = restaurant_df_new.join(avg_cost_by_city, on="city", how="left")

# Step 3: Replace null values in the Cost column with the average cost of the city
restaurant_df_filled = restaurant_df_with_avg.withColumn(
    "cost",
    when(col("cost").isNull(), col("avg_cost")).otherwise(col("cost"))
)

# Drop the avg_cost column as it's no longer needed
restaurant_df_new = restaurant_df_filled.drop("avg_cost")



In [0]:
from pyspark.sql.functions import col, sum

null_count_df = restaurant_df_new.select([sum(col(c).isNull().cast("int")).alias(c) for c in restaurant_df_new.columns])
null_count_df.show()

+----+-------+----+-------+------+----+------+------------+-------------+
|city|address|cost|cuisine|lic_no|name|rating|rating_count|restaurant_id|
+----+-------+----+-------+------+----+------+------------+-------------+
|   0|      0|   0|      0|     0|   0| 87118|       87118|            0|
+----+-------+----+-------+------+----+------+------------+-------------+



In [0]:
restaurant_df_new = restaurant_df_new.fillna(0)

In [0]:
from pyspark.sql.functions import col, sum

null_count_df = restaurant_df_new.select([sum(col(c).isNull().cast("int")).alias(c) for c in restaurant_df_new.columns])
null_count_df.show()

+----+-------+----+-------+------+----+------+------------+-------------+
|city|address|cost|cuisine|lic_no|name|rating|rating_count|restaurant_id|
+----+-------+----+-------+------+----+------+------------+-------------+
|   0|      0|   0|      0|     0|   0|     0|           0|            0|
+----+-------+----+-------+------+----+------+------------+-------------+



In [0]:
from pyspark.sql.functions import col, sum

null_count_df = menu_df_new.select([sum(col(c).isNull().cast("int")).alias(c) for c in menu_df_new.columns])
null_count_df.show()

+--------+---------+-----+-------------+--------------+
|category|item_name|price|restaurant_id|veg_or_non_veg|
+--------+---------+-----+-------------+--------------+
|       0|        0|    0|            0|             0|
+--------+---------+-----+-------------+--------------+



# 3. Text Standardization

In [0]:
from pyspark.sql.functions import lower,col

# Standardize text fields in restaurant_df
restaurant_df_new = restaurant_df_new.withColumn("city", lower(col("city"))) \
                             .withColumn("cuisine", lower(col("cuisine"))) \
                             .withColumn("name", lower(col("name")))

# Standardize text fields in menu_df
menu_df_new = menu_df_new.withColumn("category", lower(col("category"))) \
                 .withColumn("item_name", lower(col("item_name")))


In [0]:
 # Verify null counts again
from pyspark.sql.functions import col, sum

null_count_df = restaurant_df_new.select([sum(col(c).isNull().cast("int")).alias(c) for c in restaurant_df_new.columns])
null_count_df.show()


+----+-------+----+-------+------+----+------+------------+-------------+
|city|address|cost|cuisine|lic_no|name|rating|rating_count|restaurant_id|
+----+-------+----+-------+------+----+------+------------+-------------+
|   0|      0|   0|      0|     0|   0|     0|           0|            0|
+----+-------+----+-------+------+----+------+------------+-------------+



# 5. Foreign Key Integrity Check
Ensure all Restaurant_ID in menu_df exist in restaurant_df.

In [0]:
# Perform an inner join to keep only valid Restaurant_IDs
menu_df_new = menu_df_new.join(restaurant_df_new.select("restaurant_id"), on="restaurant_id", how="inner")


In [0]:
from pyspark.sql.functions import collect_list,struct

menu_df_grouped = menu_df_new.groupBy('restaurant_id').agg(
    collect_list(
        struct('category', 'item_name', 'price', 'restaurant_id', 'veg_or_non_veg')
    ).alias('menu_items')
)

In [0]:
restaurant_df_new.count()

Out[44]: 148489

In [0]:
menu_df_grouped.count()

Out[45]: 147077

In [0]:
menu_df_grouped.printSchema()

root
 |-- restaurant_id: string (nullable = true)
 |-- menu_items: array (nullable = false)
 |    |-- element: struct (containsNull = false)
 |    |    |-- category: string (nullable = true)
 |    |    |-- item_name: string (nullable = true)
 |    |    |-- price: float (nullable = true)
 |    |    |-- restaurant_id: string (nullable = true)
 |    |    |-- veg_or_non_veg: string (nullable = true)



In [0]:

final_df = restaurant_df_new.join(menu_df_grouped, on="restaurant_id", how="left")

# 6. Add Metadata Columns
Add ingestion_timestamp and source_system to both DataFrames.

In [0]:
# Add ingestion timestamp
final_df = final_df.withColumn("ingestion_timestamp", current_timestamp())


In [0]:
final_df.count()

Out[49]: 148489

In [0]:
final_df.printSchema()

root
 |-- restaurant_id: string (nullable = true)
 |-- city: string (nullable = true)
 |-- address: string (nullable = true)
 |-- cost: double (nullable = false)
 |-- cuisine: string (nullable = true)
 |-- lic_no: string (nullable = true)
 |-- name: string (nullable = true)
 |-- rating: float (nullable = false)
 |-- rating_count: integer (nullable = true)
 |-- menu_items: array (nullable = true)
 |    |-- element: struct (containsNull = false)
 |    |    |-- category: string (nullable = true)
 |    |    |-- item_name: string (nullable = true)
 |    |    |-- price: float (nullable = true)
 |    |    |-- restaurant_id: string (nullable = true)
 |    |    |-- veg_or_non_veg: string (nullable = true)
 |-- ingestion_timestamp: timestamp (nullable = false)



In [0]:
from pyspark.sql.functions import col, sum

null_count_df = final_df.select([sum(col(c).isNull().cast("int")).alias(c) for c in final_df.columns])
null_count_df.show()

+-------------+----+-------+----+-------+------+----+------+------------+----------+-------------------+
|restaurant_id|city|address|cost|cuisine|lic_no|name|rating|rating_count|menu_items|ingestion_timestamp|
+-------------+----+-------+----+-------+------+----+------+------------+----------+-------------------+
|            0|   0|      0|   0|      0|     0|   0|     0|           0|      1412|                  0|
+-------------+----+-------+----+-------+------+----+------+------------+----------+-------------------+



In [0]:
final_df.display()

restaurant_id city address cost cuisine lic_no name rating rating_count menu_items ingestion_timestamp 100010 vastrapur, ahmedabad Coffee Culture, 3rd floor, Shilp epitome, off, Sindhubhavan Marg, Ahmedabad, Gujarat 380059 350.0 pizzas,pastas 10721026000846 coffee culture 4.6 20 List(List(recommended, alfredo pasta, 275.0, 100010, veg), List(mains, aloo masala fusion meal, 250.0, 100010, veg), List(black coffee, americano, 120.0, 100010, veg), List(pizza, americano temptation pizza [9 inches], 395.0, 100010, veg), List(recommended, americano temptation pizza [9 inches], 395.0, 100010, veg), List(hot coffee, cafe irish, 195.0, 100010, veg), List(recommended, cheese chilly sandwich, 250.0, 100010, veg), List(indian combo, cheese kofta with malabari paratha, 300.0, 100010, veg), List(indian combo, dal makhani with steamed rice, 200.0, 100010, veg), List(appetizers, dry manchurian, 250.0, 100010, veg), List(indian combo, extra kulcha, 35.0, 100010, veg), List(mains, enchiladas, 450.0, 100010, veg), List(flavoured cold coffee, frozen coffee rum cold coffee, 200.0, 100010, veg), List(recommended, maggi mania, 150.0, 100010, veg), List(sinful chocolate shakes, nutella shake, 350.0, 100010, veg), List(indian combo, paneer butter masala with malabari paratha, 299.0, 100010, veg), List(mains, paneer chilly fusion meal, 295.0, 100010, veg), List(recommended, qsr cheese kofta with malabari paratha, 349.0, 100010, veg), List(indian combo, qsr paneer butter masala with paratha, 299.0, 100010, veg), List(loveberrymuch, strawberry cooler, 150.0, 100010, veg), List(recommended, strawberry cooler, 150.0, 100010, veg), List(loveberrymuch, strawberry mojito, 250.0, 100010, veg), List(pizza, the italian connection pizza [9 inches], 525.0, 100010, veg), List(recommended, burnt garlic rice with paneer chilly, 395.0, 100010, veg), List(recommended, burritos, 350.0, 100010, veg), List(recommended, cafe caramel, 195.0, 100010, veg), List(hot coffee, cafe mocha, 150.0, 100010, veg), List(flavoured cold coffee, classic irish cold coffee, 200.0, 100010, veg), List(breakfast tray, garlic maggi, 175.0, 100010, veg), List(cold coffee, ice cafe mocha cold coffee, 200.0, 100010, veg), List(recommended, koffee kulture cold coffee, 175.0, 100010, veg), List(pasta, layered pasta, 550.0, 100010, veg), List(sizzlers, mix grill sizzler, 450.0, 100010, veg), List(recommended, nachos with cheese & salsa, 225.0, 100010, veg), List(recommended, paneer chilly dry, 250.0, 100010, veg), List(mains, burritos, 350.0, 100010, veg), List(recommended, cappuccino, 150.0, 100010, veg), List(dessert cold coffee, choco brownie mochochillo cold coffee, 250.0, 100010, veg), List(recommended, choco brownie mochochillo cold coffee, 250.0, 100010, veg), List(recommended, classic irish cold coffee, 200.0, 100010, veg), List(flavoured cold coffee, coffee chocolate shake cold coffee, 250.0, 100010, veg), List(appetizers, french fries, 125.0, 100010, veg), List(sizzlers, garden fresh sizzler, 450.0, 100010, veg), List(mains, hakka noodles, 200.0, 100010, veg), List(recommended, hazelnut hot chocolate, 195.0, 100010, veg), List(cold coffee, iced cafe latte cold coffee, 200.0, 100010, veg), List(recommended, kitkat shake chocolate shake, 300.0, 100010, veg), List(recommended, masala paneer rice box, 275.0, 100010, veg), List(mains, mushroom rice, 295.0, 100010, veg), List(hot coffee, nutella cappuccino, 275.0, 100010, veg), List(recommended, nutella strawberry waffle, 250.0, 100010, veg), List(salad, tandoori paneer salad, 250.0, 100010, veg), List(sizzlers, teekha paneer sizzler, 495.0, 100010, veg), List(recommended, teekha tadka pizza [9 inches], 525.0, 100010, veg), List(recommended, the italian connection pizza [9 inches], 525.0, 100010, veg), List(mains, veg fried rice, 275.0, 100010, veg), List(hot coffee, cappuccino, 150.0, 100010, veg), List(recommended, choco frapper cold coffee, 175.0, 100010, veg), List(breakfast tray, classic cheese maggi, 175.0, 100010, veg), List(recommended, c

# 7. Save Cleaned Bronze Layer

In [0]:
CONNECTION_STRING = "DefaultEndpointsProtocol=https;AccountName=swiggycasestudysa;AccountKey=I1jjhNZYL2dShfUqgqYawj7U53guZLOyG1SbQ407oMflGToAzGXJ3ubw2Qi0oyBanQiidJQciAIS+AStDdpJrQ==;EndpointSuffix=core.windows.net"
ACCOUNT_KEY = "I1jjhNZYL2dShfUqgqYawj7U53guZLOyG1SbQ407oMflGToAzGXJ3ubw2Qi0oyBanQiidJQciAIS+AStDdpJrQ=="
ACCOUNT_NAME = "swiggycasestudysa"

In [0]:
spark.conf.set(f"fs.azure.account.key.{ACCOUNT_NAME}.dfs.core.windows.net", ACCOUNT_KEY)

delta_table_path_final = f"abfss://silver-layer@{ACCOUNT_NAME}.dfs.core.windows.net/swiggy-silver/"

In [0]:

# Writing the Delta table
final_df.write.format("delta").mode("overwrite").save(delta_table_path_final)

In [0]:
final_df_fetched = spark.read.format("delta").load(delta_table_path_final)

In [0]:
%sql
SHOW DATABASES

databaseName default silver_layer

In [0]:
%sql
CREATE DATABASE IF NOT EXISTS silver_layer;
 

In [0]:
%sql
    CREATE TABLE silver_layer.swiggy_silver_table
    USING DELTA
    LOCATION "abfss://silver-layer@swiggycasestudysa.dfs.core.windows.net/swiggy-silver/"